In [1]:
import numpy as np
import os
import json
from transformers import AutoTokenizer
import numpy as np


/opt/conda/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
from tqdm import tqdm, trange
import argparse
import random
import torch
import numpy as np
import torch.nn.functional as F
from transformers import BertModel, BertPreTrainedModel, AdamW, TrainingArguments, get_linear_schedule_with_warmup

torch.manual_seed(2023)
torch.cuda.manual_seed(2023)
np.random.seed(2023)
random.seed(2023)

In [3]:
data_path = "../data/"
context_path = "wikipedia_documents.json"
with open(os.path.join(data_path, context_path), "r", encoding="utf-8") as f:
    wiki = json.load(f)
contexts = list(
    dict.fromkeys([v["text"] for v in wiki.values()])
    )   
contexts =[v["text"] for v in wiki.values()]
contexts

['이 문서는 나라 목록이며, 전 세계 206개 나라의 각 현황과 주권 승인 정보를 개요 형태로 나열하고 있다.\n\n이 목록은 명료화를 위해 두 부분으로 나뉘어 있다.\n\n# 첫 번째 부분은 바티칸 시국과 팔레스타인을 포함하여 유엔 등 국제 기구에 가입되어 국제적인 승인을 널리 받았다고 여기는 195개 나라를 나열하고 있다.\n# 두 번째 부분은 일부 지역의 주권을 사실상 (데 팍토) 행사하고 있지만, 아직 국제적인 승인을 널리 받지 않았다고 여기는 11개 나라를 나열하고 있다.\n\n두 목록은 모두 가나다 순이다.\n\n일부 국가의 경우 국가로서의 자격에 논쟁의 여부가 있으며, 이 때문에 이러한 목록을 엮는 것은 매우 어렵고 논란이 생길 수 있는 과정이다. 이 목록을 구성하고 있는 국가를 선정하는 기준에 대한 정보는 "포함 기준" 단락을 통해 설명하였다. 나라에 대한 일반적인 정보는 "국가" 문서에서 설명하고 있다.',
 '이 목록에 실린 국가 기준은 1933년 몬테비데오 협약 1장을 참고로 하였다. 협정에 따르면, 국가는 다음의 조건을 만족해야 한다.\n* (a) 영속적인 국민\n* (b) 일정한 영토\n* (c) 정부\n* (d) 타국과의 관계 참여 자격.\n특히, 마지막 조건은 국제 공동체의 참여 용인을 내포하고 있기 때문에, 다른 나라의 승인이 매우 중요한 역할을 할 수 있다.  이 목록에 포함된 모든 국가는 보통 이 기준을 만족하는 것으로 보이는 자주적이고 독립적인 국가이다. 하지만 몬테비데오 협약 기준을 만족하는지의 여부는 많은 국가가 논쟁이 되고 있는 실정이다. 또한, 몬테비데오 협약 기준만이 국가 지위의 충분한 자격이든 아니든, 국제법의 견해 차이는 존재할 수 있다. 이 물음에 대한 다른 이론에 대한 고리는 아래에서 볼 수 있다.\n\n위 기준에 논거하여 이 목록은 다음 206개 국가를 포함하고 있다.\n* 일반 국제 승인을 받은 195개 자주 국가.\n** 유엔 가입 국가 193개\n** 성좌의 명칭으로 유엔에서 국제 승인을 받은 국가: 

In [4]:
wiki

{'0': {'text': '이 문서는 나라 목록이며, 전 세계 206개 나라의 각 현황과 주권 승인 정보를 개요 형태로 나열하고 있다.\n\n이 목록은 명료화를 위해 두 부분으로 나뉘어 있다.\n\n# 첫 번째 부분은 바티칸 시국과 팔레스타인을 포함하여 유엔 등 국제 기구에 가입되어 국제적인 승인을 널리 받았다고 여기는 195개 나라를 나열하고 있다.\n# 두 번째 부분은 일부 지역의 주권을 사실상 (데 팍토) 행사하고 있지만, 아직 국제적인 승인을 널리 받지 않았다고 여기는 11개 나라를 나열하고 있다.\n\n두 목록은 모두 가나다 순이다.\n\n일부 국가의 경우 국가로서의 자격에 논쟁의 여부가 있으며, 이 때문에 이러한 목록을 엮는 것은 매우 어렵고 논란이 생길 수 있는 과정이다. 이 목록을 구성하고 있는 국가를 선정하는 기준에 대한 정보는 "포함 기준" 단락을 통해 설명하였다. 나라에 대한 일반적인 정보는 "국가" 문서에서 설명하고 있다.',
  'corpus_source': '위키피디아',
  'url': 'TODO',
  'domain': None,
  'title': '나라 목록',
  'author': None,
  'html': None,
  'document_id': 0},
 '1': {'text': '이 목록에 실린 국가 기준은 1933년 몬테비데오 협약 1장을 참고로 하였다. 협정에 따르면, 국가는 다음의 조건을 만족해야 한다.\n* (a) 영속적인 국민\n* (b) 일정한 영토\n* (c) 정부\n* (d) 타국과의 관계 참여 자격.\n특히, 마지막 조건은 국제 공동체의 참여 용인을 내포하고 있기 때문에, 다른 나라의 승인이 매우 중요한 역할을 할 수 있다.  이 목록에 포함된 모든 국가는 보통 이 기준을 만족하는 것으로 보이는 자주적이고 독립적인 국가이다. 하지만 몬테비데오 협약 기준을 만족하는지의 여부는 많은 국가가 논쟁이 되고 있는 실정이다. 또한, 몬테비데오 협약 기준만이 국가 지위의 충분한 자격이든 아니든, 국제법의 견해 차이는

In [2]:
import re
for item in range(len(wiki)):
    wiki[str(item)]['text']=re.sub(r'[^A-Za-z가-힣0-9\.\?\!\,\(\)\s]','',wiki[str(item)]['text'])
with open('../data/remove_punc2.json', 'w', encoding='utf-8') as file:
    json.dump(wiki, file, ensure_ascii=False, indent=4)
# print(wiki)

NameError: name 'wiki' is not defined

In [48]:

search_corpus = list(set([example['text'] for example in wiki.values()]))
search_corpus

['창업기 (19982007년)\n 1998년 5월   Payment Solution 개발\n 1998년 8월   PayGate.Net 설립\n 1998년 11월   PayGate Service Version  온라인 결제서비스 실시\n 1999년 2월   국내 최초 개인용 전자지불 시범서비스 실시\n 1999년 9월   Paygate Multi Payment Gateway System 특허출원\n 1999년 12월  호주 시드니올림픽 한국 후원사이트 공식지불서비스 계약체결\n 2001년 2월   전자지불업계 최초로 ISO9001 인증 획득. \n 2003년 2월   전자상거래시스템 및 전자상거래방법 특허등록\n 2003년 6월   세이퍼트(Seyfert) 전자금융 서비스 실시\n 2003년 10월  기술혁신형 중소기업(INNOBiz) A등급 및 기술벤처기업 선정\n 2004년 4월   KBS 인터넷(주) 온라인 종합 결제대행사 선정\n 2005년 10월  벤처기업 인증(중소기업진흥공단)\n 2006년 11월  애플컴퓨터 온라인스토어 전자지불서비스 계약 체결 및 서비스\n 2007년 6월   전자금융업자 등록 (금융감독원)\n\n\n해외결제진출 (20082012년)\n 2008년 1월    글로벌 해외결제서비스 개시\n 2008년 2월    글로벌 중국 결제서비스 개시 \n 2008년 11월   PCI DSS v.1.1 인증 완료, 산림청 결제시스템 공급 계약 체결\n 2009년 4월    Mobile OK 표준기반 결제모듈개발 사업자 선정\n 2009년 11월 \t매매보호사이트(www.paygate.co.kr) 서비스 오픈, PCI DSS 1.2 인증 획득, Web 표준 기반 금액 인증(AA Service) 개발\n 2010년 7월 \t해외사업자 글로벌 PG 서비스 개시\n 2011년 11월 \tAA(금액인증) 공인인증기관 평가\n 2012년 7월 \t당사 AA(Amount Authentication)인증 금융감독원 승인\n 2012년 10월 \t미국사업체 

In [29]:
with open('../data/remove_punc.json', 'w', encoding='utf-8') as file:
    json.dump(wiki, file, ensure_ascii=False, indent=4)

In [33]:
data_path = "../data/"
context_path = "remove_punc.json"
with open(os.path.join(data_path, context_path), "r", encoding="utf-8") as f:
    dataset = json.load(f)

# print(dataset['0'])

search_corpus = list(set([example['text'] for example in dataset.values()]))
print(f'총 {len(search_corpus)}개의 지문이 있습니다.')


총 56737개의 지문이 있습니다.


In [41]:
li = [3094, 1320, 12051, 12549, 16924] 
for i in li:
    print(search_corpus[i])

로마 가톨릭은 성경을 이해하는 데 있어서 애매 모호성을 말한다  로마교회의 입장을 대변한 에라스무스는 루터와 자유의지에 관해 논쟁하면서 성경은 어두움의 책이라고 했다  성경의 전문 학자만이 성경을 해석할 수 있다고 한다  물론 로마 가톨릭교회는 난해성을 강조하고 트렌트 회의에서 평신도의 성경 해석을 금하였다  그러나 구원에 필요한 내용은 단순하고 이해하기 쉽게 되어 있으므로  누구에게나 이해가 가능하다  비록 성경 가운데는 인간이 이해하기 어려운 신비로움이 있는 것은 사실이나 진실하게 구원을 갈망하는 자에게 필요한 구원의 지식은  명료     하게 드러나 있다  성령님의 조명을 통하여 성경을 성경으로 이해할 수 있다  그러므로 교회나 사제의 해석에 의존하지 않고도 누구든지 용이하게 facilitas  구원의 도리를 알 수 있다 시 19  7   칼빈은 성경을 간결하고 용이하게 brevitas et facilitas  해석하는 방법을 주장한다  명료성은 종교개혁자들의  성경은 성경으로 해석해야 된다 는 성경 해석학의 근원이다  성경은 구원을 위해서는 분명하다 
그는 칭기즈 칸 휘하의 장군으로 고려 왕에게 고려를 공격한다는 몽골 황제의 칙서를 보내고 막대한 보상금 지불을 요구하며 겁박했다   당시 무신이자 고려의 왕권을 뛰어 넘는 권신인 최우는 당시 횡포를 부리는 저고여에 대해 반감을 가지고 있었다   그는 1221년 고종 8년 과 1224년 고종 11년  두 차례에 걸쳐 고려에 파견되었다   그 중 1224년 고종 11년  11월 공물을 요구하러 고려에 왔었는데  1225년 고려 고종 12년  정월 함신진 지금의 평안북도 의주군 를 거쳐 다시 본국인 몽골 제국으로 가던 중  여진족에 의해 살해당했다  범인들은 모두 고려옷을 입고 있었다고 한다  그 후 몽골 정부에서 저고여의 피살을 빌미로 고려를 침략했다   그의 피살은 고려인이 아닌  몽골 제국이 고려 침략의 빌미를 만들기 위하여 일부로 꾸며냈다는 견해도 여럿 있지만  기록으로는 전해지지 않아 알 수 없다 
다

In [26]:
data_path = "../data/"
context_path = "remove_punc.json"
with open(os.path.join(data_path, context_path), "r", encoding="utf-8") as f:
    wiki = json.load(f)
contexts = list(
    dict.fromkeys([v["text"] for v in wiki.values()])
    )   
contexts =[v["text"] for v in wiki.values()]
contexts

['이 문서는 나라 목록이며  전 세계 206개 나라의 각 현황과 주권 승인 정보를 개요 형태로 나열하고 있다   이 목록은 명료화를 위해 두 부분으로 나뉘어 있다     첫 번째 부분은 바티칸 시국과 팔레스타인을 포함하여 유엔 등 국제 기구에 가입되어 국제적인 승인을 널리 받았다고 여기는 195개 나라를 나열하고 있다    두 번째 부분은 일부 지역의 주권을 사실상  데 팍토  행사하고 있지만  아직 국제적인 승인을 널리 받지 않았다고 여기는 11개 나라를 나열하고 있다   두 목록은 모두 가나다 순이다   일부 국가의 경우 국가로서의 자격에 논쟁의 여부가 있으며  이 때문에 이러한 목록을 엮는 것은 매우 어렵고 논란이 생길 수 있는 과정이다  이 목록을 구성하고 있는 국가를 선정하는 기준에 대한 정보는  포함 기준  단락을 통해 설명하였다  나라에 대한 일반적인 정보는  국가  문서에서 설명하고 있다 ',
 '이 목록에 실린 국가 기준은 1933년 몬테비데오 협약 1장을 참고로 하였다  협정에 따르면  국가는 다음의 조건을 만족해야 한다     a  영속적인 국민    b  일정한 영토    c  정부    d  타국과의 관계 참여 자격  특히  마지막 조건은 국제 공동체의 참여 용인을 내포하고 있기 때문에  다른 나라의 승인이 매우 중요한 역할을 할 수 있다   이 목록에 포함된 모든 국가는 보통 이 기준을 만족하는 것으로 보이는 자주적이고 독립적인 국가이다  하지만 몬테비데오 협약 기준을 만족하는지의 여부는 많은 국가가 논쟁이 되고 있는 실정이다  또한  몬테비데오 협약 기준만이 국가 지위의 충분한 자격이든 아니든  국제법의 견해 차이는 존재할 수 있다  이 물음에 대한 다른 이론에 대한 고리는 아래에서 볼 수 있다   위 기준에 논거하여 이 목록은 다음 206개 국가를 포함하고 있다    일반 국제 승인을 받은 195개 자주 국가     유엔 가입 국가 193개    성좌의 명칭으로 유엔에서 국제 승인을 받은 국가  바티칸 시국    팔레스타인지역에 

In [7]:
contexts =[v["text"] for v in wiki.values()]
contexts

['이 문서는 나라 목록이며  전 세계 206개 나라의 각 현황과 주권 승인 정보를 개요 형태로 나열하고 있다   이 목록은 명료화를 위해 두 부분으로 나뉘어 있다     첫 번째 부분은 바티칸 시국과 팔레스타인을 포함하여 유엔 등 국제 기구에 가입되어 국제적인 승인을 널리 받았다고 여기는 195개 나라를 나열하고 있다    두 번째 부분은 일부 지역의 주권을 사실상  데 팍토  행사하고 있지만  아직 국제적인 승인을 널리 받지 않았다고 여기는 11개 나라를 나열하고 있다   두 목록은 모두 가나다 순이다   일부 국가의 경우 국가로서의 자격에 논쟁의 여부가 있으며  이 때문에 이러한 목록을 엮는 것은 매우 어렵고 논란이 생길 수 있는 과정이다  이 목록을 구성하고 있는 국가를 선정하는 기준에 대한 정보는  포함 기준  단락을 통해 설명하였다  나라에 대한 일반적인 정보는  국가  문서에서 설명하고 있다 ',
 '이 목록에 실린 국가 기준은 1933년 몬테비데오 협약 1장을 참고로 하였다  협정에 따르면  국가는 다음의 조건을 만족해야 한다     a  영속적인 국민    b  일정한 영토    c  정부    d  타국과의 관계 참여 자격  특히  마지막 조건은 국제 공동체의 참여 용인을 내포하고 있기 때문에  다른 나라의 승인이 매우 중요한 역할을 할 수 있다   이 목록에 포함된 모든 국가는 보통 이 기준을 만족하는 것으로 보이는 자주적이고 독립적인 국가이다  하지만 몬테비데오 협약 기준을 만족하는지의 여부는 많은 국가가 논쟁이 되고 있는 실정이다  또한  몬테비데오 협약 기준만이 국가 지위의 충분한 자격이든 아니든  국제법의 견해 차이는 존재할 수 있다  이 물음에 대한 다른 이론에 대한 고리는 아래에서 볼 수 있다   위 기준에 논거하여 이 목록은 다음 206개 국가를 포함하고 있다    일반 국제 승인을 받은 195개 자주 국가     유엔 가입 국가 193개    성좌의 명칭으로 유엔에서 국제 승인을 받은 국가  바티칸 시국    팔레스타인지역에 

In [49]:
from datasets import DatasetDict, load_from_disk, load_metric

datasets = load_from_disk('../data/train_dataset')
# training_dataset= 
training_dataset = datasets['train']
training_dataset.column_names

['title',
 'context',
 'question',
 'id',
 'answers',
 'document_id',
 '__index_level_0__']

In [86]:
from datasets import DatasetDict, load_from_disk, load_metric

datasets = load_from_disk('../data/train_dataset')
# training_dataset= 
training_dataset = datasets['train']
print(len(datasets['train'][0]['context']))
length = len(training_dataset)
for num, data in enumerate(training_dataset):
    
    numbers = list(range(0, length))
    numbers.remove(num)  # 3을 리스트에서 제거

    selected_numbers = random.sample(numbers, 5)  # 수정된 리스트에서 5개의 숫자 랜덤 선택

    # string = datasets['train'][num]['context']
    string = ""
    # datasets['train'][num]['context'] = ""
    for idx,strs in enumerate(selected_numbers):
        if idx == num%5:
            string += datasets['train'][num]['context'] + " "
        else:
            string += datasets['train'][strs]['context'] + " "
        print(string)
    datasets['train'][num]['context'] = string
    # if num==0:
    #     break
print(datasets['train'][num]['context'])
print(len(datasets['train'][0]['context']))



862
미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\n\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\n\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05 
미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\n\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년

In [18]:
from datasets import load_from_disk
from datasets import Dataset, DatasetDict
import random

# 데이터셋 로드
datasets = load_from_disk('../data/train_dataset')
training_dataset = datasets['train']

training = datasets['train'].to_dict()
training.keys()
len
for num, data in enumerate(training):
    
    numbers = list(range(0, length))
    numbers.remove(num)  # 3을 리스트에서 제거

    selected_numbers = random.sample(numbers, 5)  # 수정된 리스트에서 5개의 숫자 랜덤 선택

    # string = datasets['train'][num]['context']
    string = ""
    # datasets['train'][num]['context'] = ""
    for idx,strs in enumerate(selected_numbers):
        if idx == num%5:
            string += training['context'][num] + " "
        else:
            string += training['context'][strs] + " "
        # print(string)
    training['context'][num] = string
    # if num==0:
    #     break
train = Dataset.from_dict(training)
print(train[0]['context'])
# print(len(training['context'][0]))

미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\n\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\n\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05 명-호 전쟁은 명나라가 베트남의 호 왕조를 공격하여 호 왕조를 멸망시킨 사건이다. 1406년에서 1407년까지 이어졌다. 이 전쟁은 처음에는 호 왕조의 전대 왕조였던 쩐 왕조를 복구해주려는 의도에서 시작되었으나, 호 왕조가 명나라가 보낸 쩐 왕조

In [23]:
from datasets import load_from_disk
from datasets import Dataset, DatasetDict
import random

# 데이터셋 로드
datasets = load_from_disk('../data/train_dataset')
training_dataset = datasets['validation']
print(training_dataset[0]['context'])

training = datasets['validation'].to_dict()
training.keys()
length = len(training_dataset)

for num, data in enumerate(training):
    
    numbers = list(range(0, length))
    numbers.remove(num)  # 3을 리스트에서 제거

    selected_numbers = random.sample(numbers, 5)  # 수정된 리스트에서 5개의 숫자 랜덤 선택

    # string = datasets['train'][num]['context']
    string = ""
    # datasets['train'][num]['context'] = ""
    for idx,strs in enumerate(selected_numbers):
        if idx == num%5:
            string += training['context'][num] + " "
        else:
            string += training['context'][strs] + " "
        # print(string)
    training['context'][num] = string
    # if num==0:
    #     break
validation = Dataset.from_dict(training)
print(validation[0]['context'])
# print(len(training['context'][0]))

순천여자고등학교 졸업, 1973년 이화여자대학교를 졸업하고 1975년 제17회 사법시험에 합격하여 판사로 임용되었고 대법원 재판연구관, 수원지법 부장판사, 사법연수원 교수, 특허법원 부장판사 등을 거쳐 능력을 인정받았다. 2003년 최종영 대법원장의 지명으로 헌법재판소 재판관을 역임하였다.\n\n경제민주화위원회(위원장 장하성이 소액주주들을 대표해 한보철강 부실대출에 책임이 있는 이철수 전 제일은행장 등 임원 4명을 상대로 제기한 손해배상청구소송에서 서울지방법원 민사합의17부는 1998년 7월 24일에 "한보철강에 부실 대출하여 은행에 막대한 손해를 끼친 점이 인정된다"며 "원고가 배상을 청구한 400억원 전액을 은행에 배상하라"고 하면서 부실 경영인에 대한 최초의 배상 판결을 했다. \n\n2004년 10월 신행정수도의건설을위한특별조치법 위헌 확인 소송에서 9인의 재판관 중 유일하게 각하 견해를 내었다. 소수의견에서 전효숙 재판관은 다수견해의 문제점을 지적하면서 관습헌법 법리를 부정하였다. 전효숙 재판관은 서울대학교 근대법학교육 백주년 기념관에서 열린 강연에서, 국회가 고도의 정치적인 사안을 정치로 풀기보다는 헌법재판소에 무조건 맡겨서 해결하려는 자세는 헌법재판소에게 부담스럽다며 소회를 밝힌 바 있다.
순천여자고등학교 졸업, 1973년 이화여자대학교를 졸업하고 1975년 제17회 사법시험에 합격하여 판사로 임용되었고 대법원 재판연구관, 수원지법 부장판사, 사법연수원 교수, 특허법원 부장판사 등을 거쳐 능력을 인정받았다. 2003년 최종영 대법원장의 지명으로 헌법재판소 재판관을 역임하였다.\n\n경제민주화위원회(위원장 장하성이 소액주주들을 대표해 한보철강 부실대출에 책임이 있는 이철수 전 제일은행장 등 임원 4명을 상대로 제기한 손해배상청구소송에서 서울지방법원 민사합의17부는 1998년 7월 24일에 "한보철강에 부실 대출하여 은행에 막대한 손해를 끼친 점이 인정된다"며 "원고가 배상을 청구한 400억원 전액을 은행에 배상하라"고 하면서 부실 경영인에 대한 최초

In [36]:
model = "klue/roberta-large"
tokenizer = AutoTokenizer.from_pretrained(model)
string = '순천여자고등학교 졸업, 1973년 이화여자대학교를 졸업하고 1975년 제17회 사법시험에 합격하여 판사로 임용되었고 대법원 재판연구관, 수원지법 부장판사, 사법연수원 교수, 특허법원 부장판사 등을 거쳐 능력을 인정받았다. 2003년 최종영 대법원장의 지명으로 헌법재판소 재판관을 역임하였다.\n\n경제민주화위원회(위원장 장하성이 소액주주들을 대표해 한보철강 부실대출에 책임이 있는 이철수 전 제일은행장 등 임원 4명을 상대로 제기한 손해배상청구소송에서 서울지방법원 민사합의17부는 1998년 7월 24일에 "한보철강에 부실 대출하여 은행에 막대한 손해를 끼친 점이 인정된다"며 "원고가 배상을 청구한 400억원 전액을 은행에 배상하라"고 하면서 부실 경영인에 대한 최초의 배상 판결을 했다. \n\n2004년 10월 신행정수도의건설을위한특별조치법 위헌 확인 소송에서 9인의 재판관 중 유일하게 각하 견해를 내었다. 소수의견에서 전효숙 재판관은 다수견해의 문제점을 지적하면서 관습헌법 법리를 부정하였다. 전효숙 재판관은 서울대학교 근대법학교육 백주년 기념관에서 열린 강연에서, 국회가 고도의 정치적인 사안을 정치로 풀기보다는 헌법재판소에 무조건 맡겨서 해결하려는 자세는 헌법재판소에게 부담스럽다며 소회를 밝힌 바 있다. 현존하는 가장 오래된 사본 중에도 《탄이초》의 저자명은 없으며, 현재까지 밝혀진 바로는 처음부터 적혀 있지 않았다고 한다. 그러나 내용으로 미루어보아 신란의 제자인 유이엔이 저자라는 설이 학계의 정설로 되어 있다. 《탄이초》를 신란의 저서로 생각하는 사람들이 있으나, 실은 신란의 신앙 어록일 뿐 직접 쓴 것은 아니다. 이것은 신란을 스승으로 모신 제자 유이엔이 스승의 사후 그의 가르침인 절대 타력에 대한 믿음을 적은 신앙서다.\n\n신란이 장년기 20년간을 바쳐 교화한 결과 일본의 관동 지방에는 수천 명의 신자가 있었다고 한다. 신자들 가운데 지도적 입장에 있었던 사람들 60여 명의 이름이 지금도 남아 있으며, 유이엔은 그중 한 사람이다. 유이엔은 당시 관동에서 신란 사후 20년 이상을 생존했으며, 깊은 학덕을 지녀 《탄이초》의 저자에 가장 부합하는 인물로 알려져 있다. 이렇게 이 책의 저자로 알려져 있는 유이엔은 본문 9장과 13장의 신란과 문답을 나누는 장면에도 등장하고 있다. 지금의 일본 미토시(水戶市)에 있는 호부쓰사(報佛寺)를 세운 그는, 그곳에 염불 도량을 열었으며, 지금도 그 흔적이 도량지(道場池)라는 못으로 남아 있다. 그러나 그 밖에는 그에 관한 정확한 기록이 많지 않다. 수를 놓을 때에 사용하는 기법을 문양의 형태에 따라 나누어 보면 선을 잇는 수, 면을 메우는 수, 어떤 무늬를 나타내는 수로 나눌 수 있다. 그 종류로는 아주 작은 점으로 표현되는 점수를 비롯해서 선을 표현하는 이음수, 실을 간격이 없이 고루 펴는 평수, 양쪽으로 갈라져 있는 잎을 수놓는 가름수, 수평으로 나란히 수놓는 푼사수, 서양 자수의 코칭 스티치와 같은 수법으로 노끈·굵은 실·금사·은사 같은 다른 가는 실로 징그어 주는 기법인 징금수, 색의 자연스러운 변화를 표현하는 데 이용되는 자련수, 돗자리의 겉모양을 표현하는 기법인 자릿수, 겉수의 입체감을 나타내기 위해 양감(量感)을 표현하는 속수, 일정하게 간격을 띄우고 수평으로 수놓는 기법인 관수, 양지관수로 밑수를 수놓은 다음 밑수의 색과 유사한 색으로 실과 실사이를 어슷하게 건너주는 엇겨놓기수, 새의 깃털을 표현하는 새털수, 결의 방향을 규칙적으로 바꾸어 가며 무늬를 만드는 무늬목수, 삼나무 잎모양처럼 엮어나간 연속무늬의 기법인 삼잎수, 소나무 잎을 수놓을 때 쓰는 솔잎수, 별모양처럼 표현하는 별무늬수, 금·은사를 사용하여 평사수로 밑수한 위에 징금수하여 기하학적인 문양을 만드는 칠보수 등이 있다. ;요시카와 하루오(吉川 春生)\n:성우 - 이치키 마츠히로, 신도 케이(어린 시절의 하루오 역)/정재헌\n:본 작품의 남자 주인공. 수수하고 평범하기 그지 없는 중학교 3학년생. 내세울 만한 건 개근상 밖에 없고, 장래희망은 오래 사는 것이고 항상 평온한 나날을 바란다. 하지만 저주를 풀기 위해 인간계로 온 아유미의 등장으로, 그의 평온한 일상도 끝이 나고 만다.\n:그러나 실은 그의 집안은 마법사 집안이고, 그는 봉인된 마왕의 핵이라고 한다. 하지만 그의 마력과 마법에 관한 모든 것들은 봉인되어, 본인은 자신이 마법사 집안의 사람이라는 것도 자기 안에 마왕이 봉인되어 있다는 것도 기억하지 못 한다. 또한 그가 마법에 관한 일에 얽혀도, 동생들의 갖은 노력(?)으로 그 사실조차도 모르고 지나간다.\n\n;마미야 아유미(魔宮 あゆみ)\n:성우 - 노가와 사쿠라/박영희\n:본 작품의 여주인공으로, 마법 세계에서도 이름 있는, 마미야 가문의 장녀. 어릴 적에 우연히 걸려버린 저주를 풀고자 요시카와 집안에 메이드로 들어온다. 무서울 정도로 매사에 적극적이고 자신의 매력을 효과적으로 사용하는 방법도 잘 알고 있지만, 위낙 폭주 성향이 강하다 보니 가끔 역효과가 나곤 한다. 자신에게 걸린 저주를 풀기 위해, 하루오의 잠재된 마력을 깨우려고 노력중이나 항상 실패로 돌아간다.\n:처음엔 하루오를 단순히 저주를 풀기 위한 존재로 밖에 생각하지 않았으나, 점차 그에게 호감을 품어간다. \n:쥐와 뱀장어를 극도로 싫어한다.\n\n;쿠로스 유리(黑黒須 ゆり)\n:성우 - 나미카 노리코/이명선\n:하루오를 남몰래 짝사랑하고 있는 학생회장. 우아한 외모와 달리 소년같은 언행으로 인해, 여학생들로부터 엄청 인기가 많다. 그러나 쉽사리 폭주하기 쉬운 성격에다 망상벽까지 있음. 그래서 그로 인해, 가끔 자신만의 세계에 빠져 허우적거리곤 한다. \n:그리고 그녀 역시 마녀로, 마녀의 모습이 되면 평소의 모습과 달리 흰 머리에 포니테일로 변한다.\n\n;니지하라 마린(虹原 真鈴)\n:성우 - 모모이 하루코/문남숙\n:마녀 사냥꾼인 소녀로, 그녀의 집안은 예로부터 마를 멸하는 일을 해왔다고 한다. 마녀 사냥꾼이라고 하지만, 겁이 많고 바보같은 모습을 보여주곤 한다. 하루오를 성자라 오해하고 있으며, 그에게 존경과 호감을 보여주고 있다. 아유미를 비롯해, 하루오 주변에 붙어 있는 마녀들을 언젠간 응징하겠다고 하나, 그녀들과 언제나 사이좋게(?) 지내고 있다.\n:그녀가 가지고 다니는, 성스러운 창은 마법을 반사하는 능력이 있다.\n\n;앙쥬 리카(杏樹 リカ)\n:성우 - 이노우에 나나\n:마미야 가문의 우수한 마법 메이드로, 마이카 세자매를 능가하는 실력을 가진 마녀이기도 함. 항상 로봇같이 차분하고 감정이 없는 듯 한 모습을 하고 있음. 마미야가의 현 당주인 아유미의 아버지의 명으로 인간계에 간 아유미를 서포트해주기 위해 하루오네로 오게 된다. 하루오의 마력 각성을 도울 수 있기 때문에 그를 막으려는 미치루와는 충돌을 일으키곤 한다. 가사 전반에 능통하며, 위기에 빠진 하루오 일행을 도와주곤 한다.\n\n;멜리사 메일스트럼\n:전멸 위기인 불사족이다. 하루오와 결혼해서 일족의 미래를 도모한다. 1989년 동유럽 사회주의 체제의 붕괴 이후 운동진영에 급진적 사회변혁 대신 체제 내의 개혁을 추구하는 움직임이 생겼\n\n그는 1987년 6·29선언에 따른 후속조치로 87년 2학기에 복학한 뒤, 입학 7년만인 1989년 2월 대학을 졸업하였고, 1990년 사법시험에 합격하였음, 사법연수원에서 자신을 구속하였던 김원치 검사를 재회하게 되었는데, 그는 구치소에 있던 피고인의 신분에서 사법연수생이 되었고, 김원치 검사는 사법연수원 교수로 근무하고 있었음, [이날 면담에서 김부장검사가 『지금 당시의 행동을 어떻게 생각하느냐』고 묻자 이씨는 『앞으로 법조인으로 현실 생활에 충실하면서 과거의 생각들을 다시 확인해볼 계획』이라고 대답했다. 다른 합격생들의 면담은 3∼4분만에 끝났지만 과거의 검사와 피고인은 20여분간 대화를 이어갔다. 이날 두 사람은 깊은 이야기는 못다했지만 앞으로 자주 만나 소주도 나누며 법조계 선후배로 가깝게 지내자고 약속했다. 면담을 마친 김부장검사는 『과거 후배인 이군을 구속할때는 무척 안타까웠지만 어떻게 할 도리가 없었다』며 『이제 예비법조인으로서 당당히 만나게 된 이상 훌륭한 후배가 되도록 이끌어 주고 싶을 뿐』이라고 말했다. 이군은 『과거의 관계를 떠나 오랜만에 선배를 만나니 반갑다』면서도 『이러한 모습이 자칫 운동권 출신이 자연스럽게 현실에 흡수돼 가는 듯한 인상으로 비쳐져서는 안될 것』이라고 말하며 연수원을 떠났다.] \n\n〈중앙일보〉는 그의 사법시험 합격에 대하여 합격자인 이흥구가 『자신이 합력보다 더 기쁜 것은 우리 사회도 이제는 국가보안법 위반자를 받아들일 수 있고 국가보안법 자체를 재평가할 수 있는 풍토가 조성되고 있다는 사실』을 인용하면서 “지난날에는 면접시험에서 전력이 문제가 되어 불합격된 경우가 적지 않았다는 항간의 말들을 생각할 때 면접시험까지 거친 이번 최종합격이 사회의 변화를 시사하는 것이 아닌가 하는 기대를 갖게 하는 것은 사실”이라는 사설을 내기도 함'
len(tokenizer(string)['input_ids'])

Token indices sequence length is longer than the specified maximum sequence length for this model (2337 > 512). Running this sequence through the model will result in indexing errors


2337

In [37]:
model = "klue/roberta-large"
tokenizer = AutoTokenizer.from_pretrained(model)
string = '순천여자고등학교 졸업, 1973년 이화여자대학교를 졸업하고 1975년 제17회 사법시험에 합격하여 판사로 임용되었고 대법원 재판연구관, 수원지법 부장판사, 사법연수원 교수, 특허법원 부장판사 등을 거쳐 능력을 인정받았다. 2003년 최종영 대법원장의 지명으로 헌법재판소 재판관을 역임하였다.\n\n경제민주화위원회(위원장 장하성이 소액주주들을 대표해 한보철강 부실대출에 책임이 있는 이철수 전 제일은행장 등 임원 4명을 상대로 제기한 손해배상청구소송에서 서울지방법원 민사합의17부는 1998년 7월 24일에 "한보철강에 부실 대출하여 은행에 막대한 손해를 끼친 점이 인정된다"며 "원고가 배상을 청구한 400억원 전액을 은행에 배상하라"고 하면서 부실 경영인에 대한 최초의 배상 판결을 했다. \n\n2004년 10월 신행정수도의건설을위한특별조치법 위헌 확인 소송에서 9인의 재판관 중 유일하게 각하 견해를 내었다. 소수의견에서 전효숙 재판관은 다수견해의 문제점을 지적하면서 관습헌법 법리를 부정하였다. 전효숙 재판관은 서울대학교 근대법학교육 백주년 기념관에서 열린 강연에서, 국회가 고도의 정치적인 사안을 정치로 풀기보다는 헌법재판소에 무조건 맡겨서 해결하려는 자세는 헌법재판소에게 부담스럽다며 소회를 밝힌 바 있다.'
len(tokenizer(string)['input_ids'])

327

In [26]:
validation,train

(Dataset({
     features: ['title', 'context', 'question', 'id', 'answers', 'document_id', '__index_level_0__'],
     num_rows: 240
 }),
 Dataset({
     features: ['title', 'context', 'question', 'id', 'answers', 'document_id', '__index_level_0__'],
     num_rows: 3952
 }))

In [28]:
dataset_dict = DatasetDict({
    "train": train,
    "validation": validation
})
dataset_dict.save_to_disk('../dataset/train_dataset')


Saving the dataset (1/1 shards): 100%|██████████| 240/240 [00:00<00:00, 37860.42 examples/s]


In [29]:
# 데이터셋 로드
datasets = load_from_disk('../dataset/train_dataset')
training_dataset = datasets['train']
training_dataset

Dataset({
    features: ['title', 'context', 'question', 'id', 'answers', 'document_id', '__index_level_0__'],
    num_rows: 3952
})

In [94]:
x= {1:2,3:4}
x.keys = [2,3]

AttributeError: 'dict' object attribute 'keys' is read-only

In [ ]:
datasets['train'] = datasets['train'].map(augment_contexts, fn_kwargs={'all_contexts': all_contexts})

In [89]:
datasets['train'][0]['context']

'미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\\n\\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\\n\\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05'

In [90]:
datasets['train'][0]['context']= 1
datasets['train'][0]['context']



'미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\\n\\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\\n\\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05'

In [83]:
print(datasets['train'][0]['context'])


미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\n\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\n\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05


In [65]:
datasets.save_to_disk('../dataset/dataset')

Saving the dataset (1/1 shards): 100%|██████████| 240/240 [00:00<00:00, 25543.87 examples/s]


In [61]:
training_dataset.select(range(10))['answers']

[{'answer_start': [284], 'text': ['한보철강']},
 {'answer_start': [146], 'text': ['1871년']},
 {'answer_start': [517], 'text': ['나뭇잎']},
 {'answer_start': [1109], 'text': ['금대야']},
 {'answer_start': [386], 'text': ['수평적 관계']},
 {'answer_start': [408], 'text': ['옥음방송']},
 {'answer_start': [192], 'text': ['코칭 스티치']},
 {'answer_start': [31], 'text': ['복잡한 감염병']},
 {'answer_start': [625], 'text': ['스페인']},
 {'answer_start': [71], 'text': ['20세기 초']}]

In [54]:
from datasets import DatasetDict, load_from_disk, load_metric

datasets = load_from_disk('../data/train_dataset')
# training_dataset= 
training_dataset = datasets['validation']
training_dataset.column_names

['title',
 'context',
 'question',
 'id',
 'answers',
 'document_id',
 '__index_level_0__']

In [57]:
training_dataset.select(range(10))['answers']

[{'answer_start': [284], 'text': ['한보철강']},
 {'answer_start': [146], 'text': ['1871년']},
 {'answer_start': [517], 'text': ['나뭇잎']},
 {'answer_start': [1109], 'text': ['금대야']},
 {'answer_start': [386], 'text': ['수평적 관계']},
 {'answer_start': [408], 'text': ['옥음방송']},
 {'answer_start': [192], 'text': ['코칭 스티치']},
 {'answer_start': [31], 'text': ['복잡한 감염병']},
 {'answer_start': [625], 'text': ['스페인']},
 {'answer_start': [71], 'text': ['20세기 초']}]

In [52]:
training_dataset['context']

['미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\\n\\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\\n\\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05',
 "'근대적 경영학' 또는 '고전적 경영학'에서 현대적 경영학으로 전환되는 시기는 1950년대이다. 2차 세계대전을 마치고, 6.25전쟁의 시기로 유럽은 전후 재건에 집중하고, 유럽 제국주의의 식민지가 독립하여 아프리카, 아시아, 

In [3]:
training_dataset = datasets['validation']
training_dataset.column_names

['title',
 'context',
 'question',
 'id',
 'answers',
 'document_id',
 '__index_level_0__']

In [23]:
# set number of neagative sample
num_neg = 3

corpus = np.array(training_dataset['context'])
p_with_neg = []

for c in corpus:
  while True:
    neg_idxs = np.random.randint(len(corpus), size=num_neg)

    if not c in corpus[neg_idxs]:
      p_neg = corpus[neg_idxs]

      p_with_neg.append(c)
      p_with_neg.extend(p_neg)
      break
print('[Positive context]')
print(p_with_neg[0], '\n')

print('[Negative context]')
print(p_with_neg[1], '\n', p_with_neg[2])

[Positive context]
미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\n\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\n\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05 

[Negative context]
김선자는 1986년 10월 31일에 서울 중구 신당동에 거주하던 자신의 친구이자 계원인 김계환(여자, 당시 49세)에게 목욕탕에 함께 가자고 제안하고 김계환을 목욕탕으로 유인

In [10]:
print(len(p_with_neg))

226948


In [12]:
len(contexts)

56737

In [30]:
from transformers import AutoTokenizer
import numpy as np

model_checkpoint = "bert-base-multilingual-cased"

tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)


In [20]:
from datasets import DatasetDict, load_from_disk, load_metric

datasets = load_from_disk('../data/train_dataset')
# training_dataset= 
training_dataset = datasets['train']

In [24]:
from torch.utils.data import (DataLoader, RandomSampler, TensorDataset)

q_seqs = tokenizer(training_dataset['question'], padding="max_length", truncation=True, return_tensors='pt')
p_seqs = tokenizer(p_with_neg, padding="max_length", truncation=True, return_tensors='pt')

In [ ]:
tokenizer

In [25]:
max_len = p_seqs['input_ids'].size(-1)
p_seqs['input_ids'] = p_seqs['input_ids'].view(-1, num_neg+1, max_len)
p_seqs['attention_mask'] = p_seqs['attention_mask'].view(-1, num_neg+1, max_len)
p_seqs['token_type_ids'] = p_seqs['token_type_ids'].view(-1, num_neg+1, max_len)

print(p_seqs['input_ids'].size())  #(num_example, pos + neg, max_len)

torch.Size([3952, 4, 512])


In [26]:
train_dataset = TensorDataset(p_seqs['input_ids'], p_seqs['attention_mask'], p_seqs['token_type_ids'],
                              q_seqs['input_ids'], q_seqs['attention_mask'], q_seqs['token_type_ids'])

In [34]:
train_dataset

In [37]:
class BertEncoder(BertPreTrainedModel):
  def __init__(self, config):
    super(BertEncoder, self).__init__(config)

    self.bert = BertModel(config)
    self.init_weights()

  def forward(self, input_ids,
              attention_mask=None, token_type_ids=None):

      outputs = self.bert(input_ids,
                          attention_mask=attention_mask,
                          token_type_ids=token_type_ids)

      pooled_output = outputs[1]
      return pooled_output

In [38]:
# load pre-trained model on cuda (if available)
p_encoder = BertEncoder.from_pretrained(model_checkpoint)
q_encoder = BertEncoder.from_pretrained(model_checkpoint)

if torch.cuda.is_available():
  p_encoder.cuda()
  q_encoder.cuda()

model.safetensors: 100%|██████████| 714M/714M [00:08<00:00, 80.6MB/s] 
Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertEncoder: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.bias']
- This IS expected if you are initializing BertEncoder from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertEncoder from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing 

In [42]:
def train(args, num_neg, dataset, p_model, q_model):

  # Dataloader
  train_sampler = RandomSampler(dataset)
  train_dataloader = DataLoader(dataset, sampler=train_sampler, batch_size=args.per_device_train_batch_size)

  # Optimizer
  no_decay = ['bias', 'LayerNorm.weight']
  optimizer_grouped_parameters = [
        {'params': [p for n, p in p_model.named_parameters() if not any(nd in n for nd in no_decay)], 'weight_decay': args.weight_decay},
        {'params': [p for n, p in p_model.named_parameters() if any(nd in n for nd in no_decay)], 'weight_decay': 0.0},
        {'params': [p for n, p in q_model.named_parameters() if not any(nd in n for nd in no_decay)], 'weight_decay': args.weight_decay},
        {'params': [p for n, p in q_model.named_parameters() if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}
        ]
  optimizer = AdamW(optimizer_grouped_parameters, lr=args.learning_rate, eps=args.adam_epsilon)
  t_total = len(train_dataloader) // args.gradient_accumulation_steps * args.num_train_epochs
  scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=args.warmup_steps, num_training_steps=t_total)

  # Start training!
  global_step = 0

  p_model.zero_grad()
  q_model.zero_grad()
  torch.cuda.empty_cache()

  train_iterator = trange(int(args.num_train_epochs), desc="Epoch")

  for _ in train_iterator:
    epoch_iterator = tqdm(train_dataloader, desc="Iteration")

    for step, batch in enumerate(epoch_iterator):
      q_encoder.train()
      p_encoder.train()

      targets = torch.zeros(args.per_device_train_batch_size).long()
      if torch.cuda.is_available():
        batch = tuple(t.cuda() for t in batch)
        targets = targets.cuda()

      p_inputs = {'input_ids': batch[0].view(
                                    args.per_device_train_batch_size*(num_neg+1), -1),
                  'attention_mask': batch[1].view(
                                    args.per_device_train_batch_size*(num_neg+1), -1),
                  'token_type_ids': batch[2].view(
                                    args.per_device_train_batch_size*(num_neg+1), -1)
                  }

      q_inputs = {'input_ids': batch[3],
                  'attention_mask': batch[4],
                  'token_type_ids': batch[5]}

      p_outputs = p_model(**p_inputs)  #(batch_size*(num_neg+1), emb_dim)
      q_outputs = q_model(**q_inputs)  #(batch_size*, emb_dim)

      # Calculate similarity score & loss
      p_outputs = p_outputs.view(args.per_device_train_batch_size, -1, num_neg+1)
      q_outputs = q_outputs.view(args.per_device_train_batch_size, 1, -1)

      sim_scores = torch.bmm(q_outputs, p_outputs).squeeze()  #(batch_size, num_neg+1)
      sim_scores = sim_scores.view(args.per_device_train_batch_size, -1)
      sim_scores = F.log_softmax(sim_scores, dim=1)

      loss = F.nll_loss(sim_scores, targets)

      loss.backward()
      optimizer.step()
      scheduler.step()
      q_model.zero_grad()
      p_model.zero_grad()
      global_step += 1

      torch.cuda.empty_cache()



  return p_model, q_model

In [40]:
args = TrainingArguments(
    output_dir="dense_retireval",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    num_train_epochs=2,
    weight_decay=0.01
)

In [43]:
p_encoder, q_encoder = train(args, num_neg, train_dataset, p_encoder, q_encoder)

Epoch:   0%|          | 0/2 [00:00<?, ?it/s]





























































































































































































































































































































































































































































































































































































































































































































































































































































































































































































In [67]:
p_encoder.save_pretrained('../output/p_model')
q_encoder.save_pretrained('../output/q_model')


In [64]:

valid_corpus = list(set([example['context'] for example in datasets['validation']]))[:10]
sample_idx = random.choice(range(len(datasets['validation'])))
query = datasets['validation'][sample_idx]['question']
ground_truth = datasets['validation'][sample_idx]['context']

if not ground_truth in valid_corpus:
  valid_corpus.append(ground_truth)

print(query)
print(ground_truth, '\n\n')

valid_corpus[10]

비슷한 양의 골편이 두종류가 발견되는것으로 알 수 있는 A.수페르스테스의 몸의 형태는?
오스트레일리아에서 발견된 것 중 가장 온전하고 풍부한 아우스트랄로할키에리아 수페르스테스의 학명은 "남쪽에서 살아남은 할키에리아"라는 의미를 가지고 있는데, 이것은 해당 종이 보토마절 말의 멸종사건에서 살아남은 할키에리아류이기 때문이다. 이 종으로 분류된 골편은 위쪽 표면으로는 볼록하고 아래쪽은 오목하다. 또 골편이 있는 평면 상에서 휘어 있으며 서로 겹쳐져 있는데, 각각의 골편에서 오목한 부분은 다음 골편의 볼록한 부분에 덮여 있다. 아우스트랄로할키에리아 내부의 빈 공간은 할키에리아의 단순한 관 모양보다 더 복잡한 형태를 가지는데 골편 높이의 절반 정도를 올라가면 원통 모양의 관이 한 쌍의 가느다란 관으로 나뉘고, 가운데 부분은 납작해 져서 양쪽의 관은 연결되어 있지 않은 것으로 보인다. 골편의 측면 역시 다른 미세구조를 가지고 있다\n\nA. 수페르스테스의 골편 중앙 관의 위쪽은 납작한 형태로 표면 바로 밑에 위치하는데 이때문에 위쪽 표면의 끝쪽에는 움푹 들어간 자국이 생긴다. 이 부분은 광물화되지 않은 상태로 남아 있어서 이것이 물 속의 화학물질을 받아들여 후각의 역할을 했을 수도 있다. A. 수페르스테스 골편이 인산염성분으로 덮여 있는 것은 원래 유기질 피부로 덮여 있었기 때문일 가능성이 있다. 선인장처럼 생긴 챈슬로리드(chancelloriid)의 골편 역시 유기질로 덮여 있는 경우가 있다. 만일 할키에리아류가 초기 연체동물이었다면 골편의 표면은 현생 연체동물 일부에서 볼 수 있는 각피층과 유사했을지도 모른다\n\nA. 수페르스테스의 골편은 서로 거울상을 하고 있는 두 종류로 이루어지는데, 이 두 종류 골편이 발견되는 양이 비슷한 것으로 보아 A. 수페르스테스는 좌우대칭의 몸을 가지고 있었던 것으로 보인다. 골편은 모두 매우 작은 크기로, 손바닥형은 250 µm 에서 650 µm, 칼날형은 300 µm 에서 1000 µm 정도의 길이를 가진다. 낫형은 다시 두 그룹으

'오스트레일리아에서 발견된 것 중 가장 온전하고 풍부한 아우스트랄로할키에리아 수페르스테스의 학명은 "남쪽에서 살아남은 할키에리아"라는 의미를 가지고 있는데, 이것은 해당 종이 보토마절 말의 멸종사건에서 살아남은 할키에리아류이기 때문이다. 이 종으로 분류된 골편은 위쪽 표면으로는 볼록하고 아래쪽은 오목하다. 또 골편이 있는 평면 상에서 휘어 있으며 서로 겹쳐져 있는데, 각각의 골편에서 오목한 부분은 다음 골편의 볼록한 부분에 덮여 있다. 아우스트랄로할키에리아 내부의 빈 공간은 할키에리아의 단순한 관 모양보다 더 복잡한 형태를 가지는데 골편 높이의 절반 정도를 올라가면 원통 모양의 관이 한 쌍의 가느다란 관으로 나뉘고, 가운데 부분은 납작해 져서 양쪽의 관은 연결되어 있지 않은 것으로 보인다. 골편의 측면 역시 다른 미세구조를 가지고 있다\\n\\nA. 수페르스테스의 골편 중앙 관의 위쪽은 납작한 형태로 표면 바로 밑에 위치하는데 이때문에 위쪽 표면의 끝쪽에는 움푹 들어간 자국이 생긴다. 이 부분은 광물화되지 않은 상태로 남아 있어서 이것이 물 속의 화학물질을 받아들여 후각의 역할을 했을 수도 있다. A. 수페르스테스 골편이 인산염성분으로 덮여 있는 것은 원래 유기질 피부로 덮여 있었기 때문일 가능성이 있다. 선인장처럼 생긴 챈슬로리드(chancelloriid)의 골편 역시 유기질로 덮여 있는 경우가 있다. 만일 할키에리아류가 초기 연체동물이었다면 골편의 표면은 현생 연체동물 일부에서 볼 수 있는 각피층과 유사했을지도 모른다\\n\\nA. 수페르스테스의 골편은 서로 거울상을 하고 있는 두 종류로 이루어지는데, 이 두 종류 골편이 발견되는 양이 비슷한 것으로 보아 A. 수페르스테스는 좌우대칭의 몸을 가지고 있었던 것으로 보인다. 골편은 모두 매우 작은 크기로, 손바닥형은 250 µm 에서 650 µm, 칼날형은 300 µm 에서 1000 µm 정도의 길이를 가진다. 낫형은 다시 두 그룹으로 나뉘는데 밑부분에 완만한 S-곡선을 가지고 있는 것은 400 µm 에서 10

In [57]:
with torch.no_grad():
  p_encoder.eval()
  q_encoder.eval()

  q_seqs_val = tokenizer([query], padding="max_length", truncation=True, return_tensors='pt').to('cuda')
  q_emb = q_encoder(**q_seqs_val).to('cpu')  #(num_query, emb_dim)

  p_embs = []
  for p in valid_corpus:
    p = tokenizer(p, padding="max_length", truncation=True, return_tensors='pt').to('cuda')
    p_emb = p_encoder(**p).to('cpu').numpy()
    p_embs.append(p_emb)

p_embs = torch.Tensor(p_embs).squeeze()  # (num_passage, emb_dim)

print(p_embs.size(), q_emb.size())

torch.Size([11, 768]) torch.Size([1, 768])


In [59]:
dot_prod_scores = torch.matmul(q_emb, torch.transpose(p_embs, 0, 1))
print(dot_prod_scores.size())

rank = torch.argsort(dot_prod_scores, dim=1, descending=True).squeeze()
print(dot_prod_scores)
print(rank)

torch.Size([1, 11])
tensor([[ 0.2020, 11.0889,  4.9857,  7.6796,  8.2540,  4.8125, 10.4583,  3.9249,
          6.1993,  7.1994,  1.6742]])
tensor([ 1,  6,  4,  3,  9,  8,  2,  5,  7, 10,  0])


In [60]:
k = 5
print("[Search query]\n", query, "\n")
print("[Ground truth passage]")
print(ground_truth, "\n")

for i in range(k):
  print("Top-%d passage with score %.4f" % (i+1, dot_prod_scores.squeeze()[rank[i]]))
  print(valid_corpus[rank[i]])

[Search query]
 트레이 파커가 목소리를 맡은 등장인물의 자식은 누구인가? 

[Ground truth passage]
사탄(Satan)은 사우스 파크 만화영화 시리즈에서 이따금씩 나오는 등장인물이다. 사탄에 기반을 두고 있으며, 트레이 파커가 목소리를 맡았다. 사탄은 기독교도를 심판하는 악마같이 지옥을 지배하고, 항상 신과 전쟁을 펼치려고 하지만, 무자비함과, 타고난 악독함하고는 거리가 멀다. 사탄은 다른 미디어에서도 묘사가 되는데, 그는 "사우스 파크"에서 다정한 마음과, 연민, 애정도 하는 주인공답지 않은 주인공이라고 할 수 있다.\n\n"사우스 파크"에서 사탄의 등장의 대부분은(또한 "극장판 사우스 파크"에서의 그의 역할에서) 그의 동성애적인 로맨틱한 애정을 주목하고 있다. 옛날에 사탄은 사담 후세인과 같이 있었는데, 나중에 사탄은 사담에게 깊숙하게 빠지게 되지만, 그의 오만함 때문에 결국에는 사담을 죽이게 된다. 사탄은 나중에 2명의 다른 파트너인 크리스와 케빈과 지내게 된다. 사탄은 또한 좀처럼 보이지 않는 데미안이라는 아들을 두고 있는데, 데미안은 명확하게 적 그리스도의 딱지를 붙이고 있지 않고 있는데, 데미안은 명백하게 "오멘"의 등장인물인 데미안을 기초로 하였다. 

Top-1 passage with score 11.0889
아버지 주환이 고위 관료였기 때문에, 낭(郞)에 서임되었다. 기도위가 되어, 주환의 병사를 대신 거느렸다\n\n적오 4년(241년), 오나라에서 병사를 크게 일으켜 위나라를 세 방향으로 치고 들어갔을 때, 주연을 따라 위나라의 번성을 공격했고, 여거와 함께 성의 외곽 방어를 깨트렸다. 주연 군은 사마의의 구원군을 보고 달아나다가 대패했으나, 주이는 이 공적으로 돌아와서는 편장군이 되었다\n\n위나라의 여강태수 문흠이 육안에 주둔하면서 수많은 요새를 구축하고, 오나라 사람들에게 모반·망명을 유도하여 오나라에 피해를 입히고 있었다. 주이는 몸소 수하 2천 명을 거느리고 문흠의 일곱 주둔지를 격파하여 수백 급을 베었고

In [35]:
import pickle
with open('../data/p_emb.pkl', 'rb') as f:
    loaded_arr = pickle.load(f)
print(type(loaded_arr))
print(loaded_arr)

<class 'numpy.ndarray'>
[[-0.99912816 -0.9875737  -0.9992778  ...  0.99514395 -0.9981637
   0.9962231 ]
 [-0.9991282  -0.9875741  -0.9992778  ...  0.99514425 -0.9981636
   0.99622387]
 [-0.99912816 -0.9875726  -0.99927765 ...  0.9951431  -0.99816364
   0.9962229 ]
 ...
 [-0.99912816 -0.9875753  -0.9992778  ...  0.9951433  -0.9981638
   0.99622226]
 [-0.9991282  -0.98757446 -0.99927765 ...  0.9951431  -0.99816376
   0.9962228 ]
 [-0.9991279  -0.9875665  -0.9992774  ...  0.9951437  -0.9981638
   0.9962247 ]]
